In [3]:
import warnings
warnings.filterwarnings(action='ignore')
%config Computer.use_jedi = False
import requests
import json
import folium
import numpy as np
import pandas as pd
# from pandas.io.json import json_normalize

In [4]:
# 따릉이 서버에 post 방식으로 요청을 해서 서버가 응답하는 데이터를 받는다.
targetSite = 'https://www.bikeseoul.com/app/station/getStationRealtimeStatus.do'
request = requests.post(targetSite, data={
    'stationGrpSeq': 'ALL'
})
# print(request)
# print(type(request.text))
# print(request.text)

In [5]:
# 따릉이 서버가 응답은 json 형태의 문자열을 파이썬에서 사용하기 위해서 딕셔너리 타입으로 변환한다.
# bike_json = json.loads(request.text) # json 모듈의 loads() 메소드 사용
bike_json = request.json() # requests 모듈의 json() 메소드 사용
# print(type(bike_json))
# print(bike_json.keys())
# print(bike_json)

In [6]:
# bike_json['realtimeList']
bike_json.get('realtimeList')

[{'stationImgFileName': '',
  'stationId': 'ST-4',
  'stationName': '102. 망원역 1번출구 앞',
  'stationLongitude': '126.91062927',
  'stationLatitude': '37.55564880',
  'rackTotCnt': '15',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '14',
  'parkingELECBikeCnt': '2',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationImgFileName': '',
  'stationId': 'ST-5',
  'stationName': '103. 망원역 2번출구 앞',
  'stationLongitude': '126.91083527',
  'stationLatitude': '37.55495071',
  'rackTotCnt': '14',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '12',
  'parkingELECBikeCnt': '8',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationImgFileName': '',
  'stationId': 'ST-6',
  'stationName': '104. 합정역 1번출구 앞',
  'stationLongitude': '126.91498566',
  'stationLatitude': '37.55062866',
  'rackTotCnt': '13',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '11',
  'parkingELECBikeCnt': '0',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationImgFileName': '',
  'stationId': 'ST-7',
  'station

In [8]:
# pandas.io.json 모듈의 json_normalize() 메소드로 json 타입의 데이터가 변환된 딕셔너리를 판다스 데이터프레임으로 변환한다.
# json_normalize(딕셔너리, 데이터프레임으로 변환할 데이터가 할당된 딕셔너리의 key)
bike_df = pd.json_normalize(bike_json, 'realtimeList')
bike_df

stationImgFileName stationId             stationName stationLongitude  \
0                            ST-4         102. 망원역 1번출구 앞     126.91062927   
1                            ST-5         103. 망원역 2번출구 앞     126.91083527   
2                            ST-6         104. 합정역 1번출구 앞     126.91498566   
3                            ST-7         105. 합정역 5번출구 앞     126.91482544   
4                            ST-8         106. 합정역 7번출구 앞     126.91282654   
...                 ...       ...                     ...              ...   
2717                      ST-3239          5870. LG트윈타워 앞     126.93008423   
2718                      ST-3250            5871. 건영상가 앞     126.90161133   
2719                      ST-3161           6053. 중부세무서 앞     126.99066162   
2720                      ST-3210  6054.청구e편한세상아파트 113동 앞     127.01821136   
2721                      ST-3255              6055. 한국경제     126.96768188   

     stationLatitude rackTotCnt parkingBikeTotCnt parkingQRBikeCnt  \
0        37.55564880         15                 0               14   
1        37.55495071         14                 0               12   
2        37.55062866         13                 0               11   
3        37.55000687          5                 0                7   
4        37.54864502         12                 0               25   
...              ...        ...               ...              ...   
2717     37.52834702         10                 0                3   
2718     37.50611877         13                 0                1   
2719     37.56092453          5                 0                3   
2720     37.56104279          5                 0                1   
2721     37.56062698          8                 0                0   

     parkingELECBikeCnt stationSeCd  mode  
0                     2     RAK_002  None  
1                     8     RAK_002  None  
2                     0     RAK_002  None  
3                     0     RAK_002  None  
4                     1     RAK_002  None  
...                 ...         ...   ...  
2717                  4     RAK_002  None  
2718                  2     RAK_002  None  
2719                  5     RAK_002  None  
2720                  2     RAK_002  None  
2721                  8     RAK_002  None  

[2722 rows x 11 columns]

In [9]:
bike_df.columns

Index(['stationImgFileName', 'stationId', 'stationName', 'stationLongitude',
       'stationLatitude', 'rackTotCnt', 'parkingBikeTotCnt',
       'parkingQRBikeCnt', 'parkingELECBikeCnt', 'stationSeCd', 'mode'],
      dtype='object')

In [10]:
# stationId: 대여소 id
# stationName: 대여소 이름
# stationLongitude: 대여소 경도
# stationLatitude: 대여소 위도
# rackTotCnt: 주차 가능한 자전거 대수
# parkingBikeTotCnt: 주차된 따릉이 LCD형 대수 => 사용하지 않음
# parkingQRBikeCnt: 주차된 따릉이 QR형 대수 => 일반 따릉이
# parkingELECBikeCnt: 주차된 새싹 따릉이 대수

bike_df_map = bike_df[['stationId', 'stationName', 'stationLongitude', 'stationLatitude', 'parkingQRBikeCnt', 
                       'parkingELECBikeCnt']]
bike_df_map

stationId             stationName stationLongitude stationLatitude  \
0         ST-4         102. 망원역 1번출구 앞     126.91062927     37.55564880   
1         ST-5         103. 망원역 2번출구 앞     126.91083527     37.55495071   
2         ST-6         104. 합정역 1번출구 앞     126.91498566     37.55062866   
3         ST-7         105. 합정역 5번출구 앞     126.91482544     37.55000687   
4         ST-8         106. 합정역 7번출구 앞     126.91282654     37.54864502   
...        ...                     ...              ...             ...   
2717   ST-3239          5870. LG트윈타워 앞     126.93008423     37.52834702   
2718   ST-3250            5871. 건영상가 앞     126.90161133     37.50611877   
2719   ST-3161           6053. 중부세무서 앞     126.99066162     37.56092453   
2720   ST-3210  6054.청구e편한세상아파트 113동 앞     127.01821136     37.56104279   
2721   ST-3255              6055. 한국경제     126.96768188     37.56062698   

     parkingQRBikeCnt parkingELECBikeCnt  
0                  14                  2  
1                  12                  8  
2                  11                  0  
3                   7                  0  
4                  25                  1  
...               ...                ...  
2717                3                  4  
2718                1                  2  
2719                3                  5  
2720                1                  2  
2721                0                  8  

[2722 rows x 6 columns]

In [11]:
# bike_df_map.dtypes
bike_df_map.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2722 entries, 0 to 2721
Data columns (total 6 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   stationId           2722 non-null   object
 1   stationName         2722 non-null   object
 2   stationLongitude    2722 non-null   object
 3   stationLatitude     2722 non-null   object
 4   parkingQRBikeCnt    2722 non-null   object
 5   parkingELECBikeCnt  2722 non-null   object
dtypes: object(6)
memory usage: 127.7+ KB


In [12]:
bike_df_map['stationLongitude'] = bike_df_map['stationLongitude'].astype(float)
bike_df_map['stationLatitude'] = bike_df_map['stationLatitude'].astype(float)
bike_df_map['parkingQRBikeCnt'] = bike_df_map['parkingQRBikeCnt'].astype(int)
bike_df_map['parkingELECBikeCnt'] = bike_df_map['parkingELECBikeCnt'].astype(int)
bike_df_map['parkingTotBikeCnt'] = bike_df_map['parkingQRBikeCnt'] + bike_df_map['parkingELECBikeCnt']
bike_df_map

stationId             stationName  stationLongitude  stationLatitude  \
0         ST-4         102. 망원역 1번출구 앞        126.910629        37.555649   
1         ST-5         103. 망원역 2번출구 앞        126.910835        37.554951   
2         ST-6         104. 합정역 1번출구 앞        126.914986        37.550629   
3         ST-7         105. 합정역 5번출구 앞        126.914825        37.550007   
4         ST-8         106. 합정역 7번출구 앞        126.912827        37.548645   
...        ...                     ...               ...              ...   
2717   ST-3239          5870. LG트윈타워 앞        126.930084        37.528347   
2718   ST-3250            5871. 건영상가 앞        126.901611        37.506119   
2719   ST-3161           6053. 중부세무서 앞        126.990662        37.560925   
2720   ST-3210  6054.청구e편한세상아파트 113동 앞        127.018211        37.561043   
2721   ST-3255              6055. 한국경제        126.967682        37.560627   

      parkingQRBikeCnt  parkingELECBikeCnt  parkingTotBikeCnt  
0                   14                   2                 16  
1                   12                   8                 20  
2                   11                   0                 11  
3                    7                   0                  7  
4                   25                   1                 26  
...                ...                 ...                ...  
2717                 3                   4                  7  
2718                 1                   2                  3  
2719                 3                   5                  8  
2720                 1                   2                  3  
2721                 0                   8                  8  

[2722 rows x 7 columns]

In [13]:
bike_df_map.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2722 entries, 0 to 2721
Data columns (total 7 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   stationId           2722 non-null   object 
 1   stationName         2722 non-null   object 
 2   stationLongitude    2722 non-null   float64
 3   stationLatitude     2722 non-null   float64
 4   parkingQRBikeCnt    2722 non-null   int32  
 5   parkingELECBikeCnt  2722 non-null   int32  
 6   parkingTotBikeCnt   2722 non-null   int32  
dtypes: float64(2), int32(3), object(2)
memory usage: 117.1+ KB


In [14]:
bike_df_map.to_csv('./data/bike_df_map.csv', index=False)

Geo Coding

지오코딩 => 주소로 위도, 경도 얻기, 역지오코딩 => 위도, 경도로 주소 얻기  
pip install geopy

In [15]:
from geopy.geocoders import Nominatim

In [16]:
# 주소를 인수로 넘겨받아 위도, 경도를 리턴하는 함수
def geocoding(address):
    geolocoder = Nominatim(user_agent='South Korea', timeout=None)
    geo = geolocoder.geocode(address)
    return {'위도': geo.latitude, '경도': geo.longitude}
    
# address = geocoding('경기도 양주시 삼숭동')
# print(address)

In [17]:
# 위도, 경도를 넘겨받아 주소를 리턴하는 함수
def geocoding_reverse(lat_lot):
    geolocoder = Nominatim(user_agent='South Korea', timeout=None)
    return geolocoder.reverse(lat_lot)

'''
address = geocoding_reverse('37.8030568,127.1021151')
# print(type(address))
# print(address)
addr = str(address).split(', ')
# print(type(addr))
# ['만삼로', '삼숭동', '양주시', '경기도', '11484', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('37.5697599,126.9836604')
addr = str(address).split(', ')
# ['54', '종로8길', '공평동', '종로1·2·3·4가동', '종로구', '서울', '04540', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('35.168921,129.1316751')
addr = str(address).split(', ')
# ['우2동', '해운대구', '부산', '48060', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('36.7711151,128.074248')
addr = str(address).split(', ')
# ['문경새재 오픈세트장', '문경시', '경상북도', '36919', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('37.568775,126.915298')
addr = str(address).split(', ')
# ['남가좌1동', '서대문구', '서울', '대한민국']
print(addr)

address = geocoding_reverse('37.568295,126.915047')
addr = str(address).split(', ')
# ['성산2동', '마포구', '서울', '대한민국']
print(addr)
'''
pass

In [18]:
bike_df_map['goo'] = np.NaN
bike_df_map['dong'] = np.NaN
bike_df_map

stationId             stationName  stationLongitude  stationLatitude  \
0         ST-4         102. 망원역 1번출구 앞        126.910629        37.555649   
1         ST-5         103. 망원역 2번출구 앞        126.910835        37.554951   
2         ST-6         104. 합정역 1번출구 앞        126.914986        37.550629   
3         ST-7         105. 합정역 5번출구 앞        126.914825        37.550007   
4         ST-8         106. 합정역 7번출구 앞        126.912827        37.548645   
...        ...                     ...               ...              ...   
2717   ST-3239          5870. LG트윈타워 앞        126.930084        37.528347   
2718   ST-3250            5871. 건영상가 앞        126.901611        37.506119   
2719   ST-3161           6053. 중부세무서 앞        126.990662        37.560925   
2720   ST-3210  6054.청구e편한세상아파트 113동 앞        127.018211        37.561043   
2721   ST-3255              6055. 한국경제        126.967682        37.560627   

      parkingQRBikeCnt  parkingELECBikeCnt  parkingTotBikeCnt  goo  dong  
0                   14                   2                 16  NaN   NaN  
1                   12                   8                 20  NaN   NaN  
2                   11                   0                 11  NaN   NaN  
3                    7                   0                  7  NaN   NaN  
4                   25                   1                 26  NaN   NaN  
...                ...                 ...                ...  ...   ...  
2717                 3                   4                  7  NaN   NaN  
2718                 1                   2                  3  NaN   NaN  
2719                 3                   5                  8  NaN   NaN  
2720                 1                   2                  3  NaN   NaN  
2721                 0                   8                  8  NaN   NaN  

[2722 rows x 9 columns]

In [19]:
'''
for i in range(bike_df_map.shape[0])[:]:
    lat_lot = '{},{}'.format(bike_df_map.loc[i, 'stationLatitude'], bike_df_map.loc[i, 'stationLongitude'])
    # print(lat_lot)
    address = geocoding_reverse(lat_lot)
    addr = str(address).split(', ')
    # print(addr[-4], addr[-5])
    try:
        bike_df_map.loc[i, 'goo'] = addr[-4]
    except:
        print('{}번째 인덱스 스테이션의 -4번째 주소 없음'.format(i))
    try:
        bike_df_map.loc[i, 'dong'] = addr[-5]
    except:
        print('{}번째 인덱스 스테이션의 -5번째 주소 없음'.format(i))
    if (i + 1) % 10 == 0:
        print('==========', i + 1, '==========')
    
bike_df_map
'''
pass

In [20]:
# bike_df_map.to_csv('./data/bike_20230907.csv', index=False)
bike_df_map = pd.read_csv('./data/bike_20230907.csv', encoding='cp949')
bike_df_map

UnicodeDecodeError: 'cp949' codec can't decode byte 0xec in position 135: illegal multibyte sequence

In [ ]:
bike_df_map[bike_df_map.goo.isnull() | bike_df_map.dong.isnull()]

In [21]:
bike_df_map[bike_df_map.goo.isnull() | bike_df_map.dong.isnull()].stationId

0          ST-4
1          ST-5
2          ST-6
3          ST-7
4          ST-8
         ...   
2717    ST-3239
2718    ST-3250
2719    ST-3161
2720    ST-3210
2721    ST-3255
Name: stationId, Length: 2722, dtype: object

In [22]:
errorList = list(bike_df_map[bike_df_map.goo.isnull() | bike_df_map.dong.isnull()].stationId)
print(type(errorList))
print(errorList)

<class 'list'>
['ST-4', 'ST-5', 'ST-6', 'ST-7', 'ST-8', 'ST-9', 'ST-10', 'ST-11', 'ST-15', 'ST-16', 'ST-18', 'ST-20', 'ST-12', 'ST-17', 'ST-19', 'ST-21', 'ST-22', 'ST-23', 'ST-24', 'ST-25', 'ST-26', 'ST-27', 'ST-28', 'ST-29', 'ST-30', 'ST-31', 'ST-32', 'ST-33', 'ST-35', 'ST-36', 'ST-37', 'ST-39', 'ST-40', 'ST-43', 'ST-41', 'ST-42', 'ST-200', 'ST-201', 'ST-202', 'ST-203', 'ST-204', 'ST-205', 'ST-206', 'ST-207', 'ST-210', 'ST-211', 'ST-212', 'ST-213', 'ST-214', 'ST-216', 'ST-217', 'ST-218', 'ST-219', 'ST-220', 'ST-221', 'ST-222', 'ST-223', 'ST-224', 'ST-226', 'ST-227', 'ST-228', 'ST-230', 'ST-231', 'ST-555', 'ST-345', 'ST-349', 'ST-232', 'ST-233', 'ST-339', 'ST-340', 'ST-341', 'ST-342', 'ST-343', 'ST-344', 'ST-346', 'ST-347', 'ST-348', 'ST-350', 'ST-351', 'ST-352', 'ST-354', 'ST-443', 'ST-45', 'ST-46', 'ST-47', 'ST-51', 'ST-50', 'ST-52', 'ST-53', 'ST-73', 'ST-55', 'ST-59', 'ST-60', 'ST-64', 'ST-66', 'ST-62', 'ST-63', 'ST-67', 'ST-68', 'ST-69', 'ST-70', 'ST-71', 'ST-72', 'ST-277', 'ST-278

In [23]:
for error in errorList:
    bike_error = bike_df_map[bike_df_map.stationId == error]
    lat_lot = '{},{}'.format(bike_error.iloc[0, 3], bike_error.iloc[0, 2])
    # print(bike_error, bike_error.index, lat_lot)
    address = geocoding_reverse(lat_lot)
    addr = str(address).split(', ')
    # print(addr)
    bike_df_map.loc[bike_error.index, 'goo'] = addr[-3]
    bike_df_map.loc[bike_error.index, 'dong'] = addr[-4]

bike_df_map[bike_df_map.goo.isnull() | bike_df_map.dong.isnull()]

Empty DataFrame
Columns: [stationId, stationName, stationLongitude, stationLatitude, parkingQRBikeCnt, parkingELECBikeCnt, parkingTotBikeCnt, goo, dong]
Index: []

In [24]:
# bike_df_map.to_csv('./data/bike_20230907.csv', index=False)

In [25]:
bike_map = folium.Map(location=[bike_df_map.stationLatitude.mean(), bike_df_map.stationLongitude.mean()], zoom_start=12)

for index, data in bike_df_map.iterrows():
    
    station = data.stationName.split('.')
    '''
    if len(station) == 1:
        stationName = station[0].strip()
    else:
        stationName = station[1].strip()
    '''
    stationName = station[0].strip() if len(station) == 1 else station[1].strip()
    string = '{} => 일반: {}대, 새싹: {}대'.format(stationName, data.parkingQRBikeCnt, data.parkingELECBikeCnt)
    # print(string)
    
    stationInfo = folium.Popup(string, max_width=300)
    folium.Marker(location=[data.stationLatitude, data.stationLongitude], popup=stationInfo,
                 icon=folium.Icon(color='green', icon='hand-down')).add_to(bike_map)

bike_map.save('./output/bike.html')
bike_map

종로구 따릉이 스테이션 위치

In [26]:
bike_df_map_goo = bike_df_map[bike_df_map.goo == '종로구']
bike_df_map_goo

stationId      stationName  stationLongitude  stationLatitude  \
200    ST-161  345. 서울보증보험본사 앞         127.00071        37.573307   

     parkingQRBikeCnt  parkingELECBikeCnt  parkingTotBikeCnt  goo     dong  
200                 8                   6                 14  종로구  종로5·6가동

In [27]:
bike_map = folium.Map(location=[bike_df_map_goo.stationLatitude.mean(), bike_df_map_goo.stationLongitude.mean()], zoom_start=14)

for index, data in bike_df_map_goo.iterrows():
    
    station = data.stationName.split('.')
    stationName = station[0].strip() if len(station) == 1 else station[1].strip()
    string = '{} => 일반: {}대, 새싹: {}대'.format(stationName, data.parkingQRBikeCnt, data.parkingELECBikeCnt)
    # print(string)
    
    stationInfo = folium.Popup(string, max_width=300)
    folium.Marker(location=[data.stationLatitude, data.stationLongitude], popup=stationInfo,
                 icon=folium.Icon(color='green', icon='hand-down')).add_to(bike_map)

bike_map.save('./output/bike.html')
bike_map